# **PDF book into images** `book_pages`

In [2]:
from pdf2image import convert_from_path
import os


def pdf_to_images(
    pdf_path: str, output_folder: str, dpi: int = 150, max_pages: int = 2
):
    os.makedirs(output_folder, exist_ok=True)
    try:
        images = convert_from_path(pdf_path, dpi=dpi)
        for i, img in enumerate(images, 1):
            img.save(os.path.join(output_folder, f"page_{i}.jpg"), "JPEG")
        print("✅ Done")
    except Exception as e:
        print("❌ Error:", e)


# Test with fewer pages
pdf_to_images("book.pdf", "book_pages", dpi=150, max_pages=3)

✅ Done


# **Image layout extraction**

In [7]:
import os
import re
import csv
import logging
from typing import List, Dict
from PIL import Image
from huggingface_hub import hf_hub_download
from doclayout_yolo import YOLOv10

# === Logging Setup ===
logging.basicConfig(
    level=logging.INFO, format="%(asctime)s - %(levelname)s - %(message)s"
)

# === Load YOLOv10 Layout Model ===
logging.info("🔄 Downloading and loading YOLOv10 layout model...")
model_path = hf_hub_download(
    repo_id="juliozhao/DocLayout-YOLO-DocStructBench",
    filename="doclayout_yolo_docstructbench_imgsz1024.pt",
)
model = YOLOv10(model_path)
logging.info("✅ Model loaded successfully.")


# === Natural Sort Helper ===
def natural_sort_key(s: str):
    return [
        int(text) if text.isdigit() else text.lower() for text in re.split(r"(\d+)", s)
    ]


# === Two-Column Identification ===
def identify_columns(boxes: List[Dict], tolerance=50) -> List[List[Dict]]:
    if not boxes:
        return []

    # Sort boxes by horizontal center
    sorted_boxes = sorted(boxes, key=lambda box: box["center_x"])

    # Compute midpoint to split columns
    min_x = min(box["center_x"] for box in boxes)
    max_x = max(box["center_x"] for box in boxes)
    midpoint = (min_x + max_x) / 2

    left_column = [box for box in sorted_boxes if box["center_x"] <= midpoint]
    right_column = [box for box in sorted_boxes if box["center_x"] > midpoint]

    # Fallback if one column is empty (group by tolerance)
    if not left_column or not right_column:
        columns = []
        current_column = [sorted_boxes[0]]
        for box in sorted_boxes[1:]:
            if abs(box["center_x"] - current_column[-1]["center_x"]) <= tolerance:
                current_column.append(box)
            else:
                columns.append(current_column)
                current_column = [box]
        columns.append(current_column)
        return columns

    return [left_column, right_column]


# === Image Layout Processing ===
def process_image(image: Image.Image, image_id: str, output_base_dir: str):
    results = model.predict(image, imgsz=1024, conf=0.2)
    result = results[0]
    class_map = result.names

    boxes = []
    for i, (xyxy, cls_idx) in enumerate(zip(result.boxes.xyxy, result.boxes.cls)):
        x1, y1, x2, y2 = map(int, xyxy)
        label = class_map[int(cls_idx)]
        center_x = (x1 + x2) / 2
        center_y = (y1 + y2) / 2
        boxes.append(
            {
                "id": i,
                "x1": x1,
                "y1": y1,
                "x2": x2,
                "y2": y2,
                "center_x": center_x,
                "center_y": center_y,
                "label": label,
            }
        )

    logging.info(f"📦 Found {len(boxes)} elements on {image_id}")
    columns = identify_columns(boxes)
    logging.info(f"🧭 Identified {len(columns)} columns on {image_id}")

    for i, col in enumerate(columns):
        columns[i] = sorted(col, key=lambda b: b["y1"])

    output_dir = os.path.join(output_base_dir, f"page_{image_id}")
    os.makedirs(output_dir, exist_ok=True)

    metadata = {"columns": len(columns), "elements": []}

    for col_idx, column in enumerate(columns):
        column_dir = os.path.join(output_dir, f"column_{col_idx}")
        os.makedirs(column_dir, exist_ok=True)

        for pos_idx, box in enumerate(column):
            cropped = image.crop((box["x1"], box["y1"], box["x2"], box["y2"])).convert(
                "RGB"
            )
            filename = f"{col_idx}_{pos_idx}_{box['label']}.jpg"
            filepath = os.path.join(column_dir, filename)
            cropped.save(filepath)

            metadata["elements"].append(
                {
                    "id": box["id"],
                    "label": box["label"],
                    "column": col_idx,
                    "position": pos_idx,
                    "filename": filename,
                    "coordinates": [box["x1"], box["y1"], box["x2"], box["y2"]],
                }
            )

    # Save metadata as CSV
    csv_path = os.path.join(output_dir, "layout_order.csv")
    with open(csv_path, "w", newline="") as f:
        writer = csv.writer(f)
        writer.writerow(
            ["id", "label", "column", "position", "filename", "x1", "y1", "x2", "y2"]
        )
        for el in metadata["elements"]:
            writer.writerow(
                [
                    el["id"],
                    el["label"],
                    el["column"],
                    el["position"],
                    el["filename"],
                    *el["coordinates"],
                ]
            )

    logging.info(f"📄 Page {image_id} processed and saved to {output_dir}")


# === Folder Processor ===
def process_image_folder(image_folder: str, output_base_dir: str):
    image_files = sorted(
        [
            f
            for f in os.listdir(image_folder)
            if f.lower().endswith((".png", ".jpg", ".jpeg"))
        ],
        key=natural_sort_key,
    )

    if not image_files:
        logging.warning("⚠️ No image files found.")
        return

    for image_file in image_files:
        image_id = os.path.splitext(image_file)[0]
        output_page_dir = os.path.join(output_base_dir, f"{image_id}")
        csv_file = os.path.join(output_page_dir, "layout_order.csv")
        if os.path.exists(csv_file):
            logging.info(f"⏭️ Skipping {image_id} (already processed).")
            continue

        image_path = os.path.join(image_folder, image_file)
        image = Image.open(image_path).convert("RGB")
        logging.info(f"🔍 Processing {image_id}...")
        process_image(image, image_id, output_base_dir)

    logging.info("✅ All images processed successfully.")


# === Entry Point ===
input_image_folder = "book_pages"  # Folder with extracted images
output_dir = "book_layouts"
os.makedirs(output_dir, exist_ok=True)
process_image_folder(input_image_folder, output_dir)

2025-05-19 14:05:37,094 - INFO - 🔄 Downloading and loading YOLOv10 layout model...
2025-05-19 14:05:37,372 - INFO - ✅ Model loaded successfully.
2025-05-19 14:05:37,382 - INFO - 🔍 Processing page_1...



0: 1024x736 2 titles, 1 plain text, 2 abandons, 861.7ms
Speed: 5.0ms preprocess, 861.7ms inference, 0.5ms postprocess per image at shape (1, 3, 1024, 736)


2025-05-19 14:05:38,350 - INFO - 📦 Found 5 elements on page_1
2025-05-19 14:05:38,351 - INFO - 🧭 Identified 2 columns on page_1
2025-05-19 14:05:38,354 - INFO - 📄 Page page_1 processed and saved to book_layouts/page_page_1
2025-05-19 14:05:38,360 - INFO - 🔍 Processing page_2...



0: 1024x736 2 titles, 5 plain texts, 1 abandon, 829.3ms
Speed: 3.8ms preprocess, 829.3ms inference, 0.7ms postprocess per image at shape (1, 3, 1024, 736)


2025-05-19 14:05:39,205 - INFO - 📦 Found 8 elements on page_2
2025-05-19 14:05:39,205 - INFO - 🧭 Identified 2 columns on page_2
2025-05-19 14:05:39,208 - INFO - 📄 Page page_2 processed and saved to book_layouts/page_page_2
2025-05-19 14:05:39,215 - INFO - 🔍 Processing page_3...


...

2025-05-19 15:48:47,491 - INFO - 📦 Found 25 elements on page_1799
2025-05-19 15:48:47,491 - INFO - 🧭 Identified 2 columns on page_1799
2025-05-19 15:48:47,506 - INFO - 📄 Page page_1799 processed and saved to book_layouts/page_page_1799
2025-05-19 15:48:47,519 - INFO - 🔍 Processing page_1800...



0: 1024x736 7 titles, 9 plain texts, 2 abandons, 1019.0ms
Speed: 4.7ms preprocess, 1019.0ms inference, 0.6ms postprocess per image at shape (1, 3, 1024, 736)


2025-05-19 15:48:48,559 - INFO - 📦 Found 18 elements on page_1800
2025-05-19 15:48:48,560 - INFO - 🧭 Identified 2 columns on page_1800
2025-05-19 15:48:48,579 - INFO - 📄 Page page_1800 processed and saved to book_layouts/page_page_1800
2025-05-19 15:48:48,587 - INFO - 🔍 Processing page_1801...



0: 1024x736 3 titles, 3 plain texts, 2 abandons, 1044.8ms
Speed: 5.6ms preprocess, 1044.8ms inference, 1.2ms postprocess per image at shape (1, 3, 1024, 736)


2025-05-19 15:48:49,655 - INFO - 📦 Found 8 elements on page_1801
2025-05-19 15:48:49,656 - INFO - 🧭 Identified 2 columns on page_1801
2025-05-19 15:48:49,660 - INFO - 📄 Page page_1801 processed and saved to book_layouts/page_page_1801
2025-05-19 15:48:49,660 - INFO - ✅ All images processed successfully.


# Extracting Text from Images

In [32]:
import os
import re
import pytesseract
from PIL import Image
import json
import logging

logging.basicConfig(level=logging.INFO, format='[%(levelname)s] %(message)s')

root_dir = 'book_layouts'
output_dir = 'book_pages_json'
os.makedirs(output_dir, exist_ok=True)

# Extract sorting key: two leading numbers in filename
def extract_sort_key(filename):
    nums = re.findall(r'\d+', filename)
    return tuple(map(int, nums[:2])) if len(nums) >= 2 else (float('inf'), float('inf'))

# Get sorted page folders
page_folders = sorted(
    [d for d in os.listdir(root_dir) if d.startswith("page_")],
    key=lambda x: int(re.search(r'\d+', x).group())
)

for page_folder in page_folders:
    page_path = os.path.join(root_dir, page_folder)
    page_num = str(re.search(r'\d+', page_folder).group())
    logging.info(f'📄 Processing {page_folder} (Page {page_num})')

    ordered_blocks = []

    # Collect all image paths from all columns
    image_entries = []
    for column_dir in sorted(os.listdir(page_path)):
        col_path = os.path.join(page_path, column_dir)
        if not os.path.isdir(col_path):
            continue

        for filename in os.listdir(col_path):
            if filename.endswith('.jpg'):
                image_entries.append((filename, os.path.join(col_path, filename)))

    # Sort images by prefix numbers
    image_entries.sort(key=lambda x: extract_sort_key(x[0]))

    for filename, img_path in image_entries:
        type_part = '_'.join(filename.split('_')[2:]).replace('.jpg', '').strip().lower()
        type_key = type_part.replace(' ', '_')

        logging.info(f'  🔍 OCR: {img_path} → {type_key}')
        try:
            text = pytesseract.image_to_string(Image.open(img_path)).strip()
            ordered_blocks.append({type_key: text})
        except Exception as e:
            logging.warning(f'    ⚠️ Failed to process {img_path}: {e}')

    # Save each page to its own JSON file
    page_output_path = os.path.join(output_dir, f'page_{page_num}.json')
    with open(page_output_path, 'w', encoding='utf-8') as f:
        json.dump({page_num: ordered_blocks}, f, ensure_ascii=False, indent=2)

    logging.info(f'✅ Saved Page {page_num} → {page_output_path}')

logging.info('🎉 All pages processed and saved individually.')

[INFO] 📄 Processing page_page_1 (Page 1)
[INFO]   🔍 OCR: book_layouts/page_page_1/column_0/0_0_abandon.jpg → abandon
[INFO]   🔍 OCR: book_layouts/page_page_1/column_0/0_1_abandon.jpg → abandon
[INFO]   🔍 OCR: book_layouts/page_page_1/column_1/1_0_title.jpg → title
[INFO]   🔍 OCR: book_layouts/page_page_1/column_1/1_1_title.jpg → title
[INFO]   🔍 OCR: book_layouts/page_page_1/column_1/1_2_plain text.jpg → plain_text
[INFO] ✅ Saved Page 1 → book_pages_json/page_1.json
[INFO] 📄 Processing page_page_2 (Page 2)
[INFO]   🔍 OCR: book_layouts/page_page_2/column_0/0_0_plain text.jpg → plain_text
[INFO]   🔍 OCR: book_layouts/page_page_2/column_0/0_1_plain text.jpg → plain_text
[INFO]   🔍 OCR: book_layouts/page_page_2/column_0/0_2_plain text.jpg → plain_text
[INFO]   🔍 OCR: book_layouts/page_page_2/column_0/0_3_plain text.jpg → plain_text
[INFO]   🔍 OCR: book_layouts/page_page_2/column_0/0_4_title.jpg → title
[INFO]   🔍 OCR: book_layouts/page_page_2/column_0/0_5_plain text.jpg → plain_text
[INFO]

# Partitioning Data

In [3]:
import os
import json
import re

input_folder = "book_pages_json"
output_file = "data_partitioned.json"

sections = []
current_section = None

# Regex: match titles with text + text (e.g., "drug A + drug B")
plus_title_pattern = re.compile(r'\b\w[\w\s]*\w\b\s*\+\s*\b\w[\w\s]*\w\b')

# Sort files like page_1.json, page_2.json, ...
files = sorted(
    [f for f in os.listdir(input_folder) if f.endswith(".json")],
    key=lambda x: int(x.split("_")[1].split(".")[0])
)

for filename in files:
    page_number = int(filename.split("_")[1].split(".")[0])
    filepath = os.path.join(input_folder, filename)

    with open(filepath, "r", encoding="utf-8") as f:
        data = json.load(f)

        if not isinstance(data, dict) or len(data) != 1:
            continue  # skip malformed files

        # Extract the only key (page number string) and its content
        page_key = next(iter(data))
        content_list = data[page_key]

        for obj in content_list:
            if "title" in obj:
                title = obj["title"].strip()
                if plus_title_pattern.fullmatch(title):
                    # Save the previous section
                    if current_section:
                        sections.append(current_section)
                    # Start a new section
                    current_section = {
                        "title": title,
                        "page": page_number,
                        "content": ""
                    }
                elif current_section:
                    current_section["content"] += title + "\n"
            elif "plain_text" in obj and current_section:
                current_section["content"] += obj["plain_text"].strip() + "\n"

# Save the last section
if current_section:
    sections.append(current_section)

# Write to output file
with open(output_file, "w", encoding="utf-8") as out:
    json.dump(sections, out, indent=2, ensure_ascii=False)

print(f"✅ Partitioned sections saved to: {output_file}")

✅ Partitioned sections saved to: partitioned_plus_titles.json


In [6]:
import json

input_file = "data_partitioned.json"
output_file = "data_titles.json"

# Load the enriched sections
with open(input_file, "r", encoding="utf-8") as f:
    sections = json.load(f)

# Extract all titles
titles = [section["title"] for section in sections]

# Save titles to a new file
with open(output_file, "w", encoding="utf-8") as f:
    json.dump(titles, f, indent=2, ensure_ascii=False)

print(f"✅ Extracted {len(titles)} titles to: {output_file}")

✅ Extracted 2584 titles to: data_titles.json


# Adding embeddings

In [4]:
import json
from sentence_transformers import SentenceTransformer

# Load sections
with open("data_partitioned.json", "r", encoding="utf-8") as f:
    sections = json.load(f)

# Load pre-trained embedding model
model = SentenceTransformer("all-MiniLM-L6-v2")

# Compute embeddings
for section in sections:
    title = section["title"]
    embedding = model.encode(title).tolist()
    section["embedding"] = embedding  # Add embedding to the section

# Save to new file
with open("partitioned_plus_titles_with_embeddings.json", "w", encoding="utf-8") as f:
    json.dump(sections, f, indent=2, ensure_ascii=False)

print("✅ Embeddings added and saved to: data_embedded.json")

✅ Embeddings added and saved to: partitioned_plus_titles_with_embeddings.json


# Extracting titles unique

In [10]:
import json
import re

input_file = "data_titles.json"
output_file = "data_titles_unique.json"

# Load titles
with open(input_file, "r", encoding="utf-8") as f:
    titles = json.load(f)

drug_names = set()

for title in titles:
    # Normalize line breaks and spaces
    clean_title = title.replace("\n", " ").replace("  ", " ").strip()
    
    # Only consider titles with '+'
    if '+' in clean_title:
        parts = [part.strip() for part in clean_title.split('+')]
        for drug in parts:
            if drug:
                drug_names.add(drug)

# Sort and save unique drug names
unique_drugs = sorted(drug_names)

with open(output_file, "w", encoding="utf-8") as f:
    json.dump(unique_drugs, f, indent=2, ensure_ascii=False)

print(f"✅ Extracted {len(unique_drugs)} unique drug names to: {output_file}")

✅ Extracted 988 unique drug names to: data_titles_unique.json


# Classification model Test

In [18]:
from fastapi import FastAPI, HTTPException
from pydantic import BaseModel
from typing import List
from groq import Groq

app = FastAPI()

drug_list = [
  "ACE ibitors",
  "ACE in",
  "ACE inh",
  "ACE inhibitors",
  "ACE inhibitors and other antihypertensives",
  "ACE inhibitors or Angiotensin II receptor antagonists",
  "ACE inhibitors or Angiotensin Il receptor antagonists",
  "Abatacept",
  "Acacia or Guar gum",
  "Acamprosate",
  "Acarbose",
  "Acetazolamide",
  "Acetylcysteine",
  "Aciclovir",
  "Aciclovir and related drugs",
  "Acipimox",
  "Adefovir",
  "Ademetionine",
  "Adenosine",
  "Agalsidase",
  "Ajmaline",
  "Albendazole",
  "Albendazole or Mebendazole",
  "Albendazole with Ivermectin",
  "Alcohol",
  "Alemtuzumab",
  "Alendronate",
  "Aliskiren",
  "Allopurinol",
  "Alosetron",
  "Alpha blockers",
  "Alprostadil",
  "Aluminium hydroxide",
  "Amantadine",
  "Amfetamines",
  "Amfetamines and related drugs",
  "Amifostine",
  "Amiloride Qui",
  "Aminoglutethimide",
  "Aminoglycosides",
  "Aminosalicylic aci",
  "Aminosalicylic acid",
  "Amiodarone",
  "Amisulpride",
  "Amodiaquine",
  "Amphotericin B",
  "Ampici",
  "Anabolic steroids",
  "Anabolic steroids or Androgens",
  "Anaesthesia",
  "Anagrelide",
  "Anakinra",
  "Anastrozole",
  "Androgens",
  "Angiotensin II receptor antagc",
  "Angiotensin II receptor antagonists",
  "Angiotensin Il receptor antagonists",
  "Anorectics",
  "Antacids",
  "Antacids or Antidiarrhoeals",
  "Antacids or Calcium compounds",
  "Antacids or Kaolin",
  "Antacids or Urinary alkalinisers",
  "Anthelmintics",
  "Anthracyclines",
  "Antiarrhythmics",
  "Antiarrhythrr",
  "Antiasthma drugs",
  "Antibacterials",
  "Anticholinesterases",
  "Antidepressants",
  "Antidiabetics",
  "Antiemetics",
  "Antiepileptics",
  "Antifibrinolytics",
  "Antifungals",
  "Antigout drugs",
  "Antihistamines",
  "Antihistamines and related drugs",
  "Antihypertensives",
  "Antimalarials",
  "Antimuscarinics",
  "Antimuscarinics or Diphenoxylate",
  "Antimycobacterials",
  "Antineoplastics",
  "Antiplatelet drugs",
  "Antiplatelet drugs or NSAIDs",
  "Antipsychotics",
  "Antiretrovirals",
  "Antithyroid drugs",
  "Apomorphine",
  "Aprepitant",
  "Aprindine",
  "Aprotini",
  "Aprotinin",
  "Argatroban",
  "Aripiprazole",
  "Armodafinil",
  "Aromatase inhibitors",
  "Artemether",
  "Artemisinin derivatives",
  "Aspiri",
  "Aspirin",
  "Aspirin or NSAIDs",
  "Aspirin or other Salicyla",
  "Aspirin or other Salicylates",
  "Atomoxetine",
  "Atovaquone",
  "Atropine",
  "Ayahuasca",
  "Azathioprine",
  "Azathioprine or Mercaptopurine",
  "Azimilide",
  "Azithromycin",
  "Azoles",
  "Aztreonam",
  "BCG vaccine",
  "Baclofen",
  "Barbiturates",
  "Barbiturates or Phenytoin",
  "Basi",
  "Basiliximab",
  "Benfluorex",
  "Benzbromarone",
  "Benzbromarone or Benziodarone",
  "Benzethonium chloride",
  "Benziodarone",
  "Benzodiazepines",
  "Benzodiazepines and related drugs",
  "Berberine",
  "Beta blockers",
  "Betacarotene",
  "Betahistine",
  "Bevacizumab",
  "Beverages",
  "Bexarotene",
  "Bicalutamide",
  "Bifendate",
  "Bismuth compounds",
  "Bisphosphonates",
  "Bleomycin",
  "Boldo or Fenugreek",
  "Bortezomib",
  "Bosentan",
  "Bretylium",
  "Brimonidine or Latanoprost",
  "Bromocriptine",
  "Bromocriptine and other dopamine agonists",
  "Broxuridine",
  "Bucolome",
  "Buflomedil",
  "Bupropion",
  "Buspirone",
  "Busulfan",
  "Butyraldoxime",
  "CNS depressants",
  "COM T inhibitors",
  "COMT inhibitors",
  "CYP2C9 substrates",
  "CYP2D6 inhibitors",
  "CYP2D6 inhibitors or substrates",
  "CYP2D6 substrates",
  "CYP3A4 inducers",
  "CYP3A4 inducers or",
  "CYP3A4 inducers or inhibitors",
  "CYP3A4 inhi",
  "CYP3A4 inhibitors",
  "CYP3A4 inhibitors or substrates",
  "CYP3A4 or CYP2D6 i",
  "CYP3A4 substrates",
  "Caffeine",
  "Caffeine or Choline theophyllinate",
  "Calcium carbimide",
  "Calcium compounds",
  "Calcium compour",
  "Candesartan",
  "Cannabinoids",
  "Cannabis",
  "Cannabis or Tobacco",
  "Capsaicin",
  "Carbamazepine",
  "Carbamazepine or Oxcarbazepine",
  "Carbamazepine or Phenytoin",
  "Carbapenems",
  "Carbenoxolone",
  "Carbimazole",
  "Carbon tetrachloride",
  "Carbonic anhydrase inhibitors",
  "Carisoprodol",
  "Carmofur",
  "Cefalexin",
  "Cefradine",
  "Celecoxib",
  "Cephalosporins",
  "Cetuximab",
  "Chamomile",
  "Chinese herbal medicines",
  "Chitosan",
  "Chlorambucil",
  "Chloramphenicol",
  "Chlorobutanol",
  "Chloroquine",
  "Chloroquine or Hydroxychloroquine",
  "Chloroquine with Proguanil",
  "Chlorothiazide",
  "Chlorphenamine",
  "Chlorpromazine",
  "Chlorzoxazone",
  "Chromium compounds",
  "Ciclosporin",
  "Ciclosporin or Tacrolimus",
  "Cidofovir",
  "Cilostazol",
  "Cime",
  "Cimeti",
  "Cimetidine",
  "Cimetidine or Omeprazole",
  "Cinacalcet",
  "Ciprofloxaci",
  "Ciprofloxacin",
  "Cisapride",
  "Cisplati",
  "Cisplatin",
  "Cisplatin and other platinum compounds",
  "Clarithromycin",
  "Class Ic antiarrhythmics",
  "Clindamycin",
  "Clindamycin or Lincomycin",
  "Clodronate",
  "Clofazimine",
  "Clomethiazole",
  "Clomipramine",
  "Clonidine",
  "Clonidine and related drugs",
  "Clopidogrel",
  "Clopidogrel or Ticlopidine",
  "Cloral hydrate",
  "Cloral hydrate and related drugs",
  "Clozapine",
  "Cocaine",
  "Codeine",
  "Coffee or Tea",
  "Cola drinks",
  "Colchi",
  "Colchicine",
  "Colesevelam",
  "Colestipol",
  "Colestyramine",
  "Colistin",
  "Colloids",
  "Combined hormonal contraceptives",
  "Corticosteroids",
  "Corticosteroids or Corticotropin",
  "Coumarins",
  "Coumarins and related drugs",
  "Coxibs",
  "Cranberry juice",
  "Curbicin",
  "Cyclobenzaprine",
  "Cyclophosphamide",
  "Cyclophosphamide or Ifosfamide",
  "Cyclophosphamide or lIfosfamide",
  "Cycloserine",
  "Cyproheptadine",
  "Cyproterone acetate",
  "Cytarabine",
  "Cytochrome P450 substrates",
  "Cytokines",
  "Dacarbazine",
  "Dairy products",
  "Danaparoid",
  "Danazol",
  "Danazol or Gestrinone",
  "Dantrolene",
  "Dantrolene and Oxybutynin",
  "Dapsone",
  "Daptomycin",
  "Darifenacin or Solifenacin",
  "Dasatinib",
  "Desmopressin",
  "Dexamethasone",
  "Dexamfetamine",
  "Dexfenfluramine or Fenfluramine",
  "Dexmedetomidine",
  "Dextrans",
  "Dextromethorphan",
  "Dextromethorphar",
  "Dialysis or Transfusion membranes",
  "Diazepam",
  "Diazoxide",
  "Dichloralphenazone",
  "Diclofenac",
  "Didanosine",
  "Dietary fibre or Laxatives",
  "Diethylcarbamazine",
  "Digoxin",
  "Digoxin and related drugs",
  "Dihydroergocryptine",
  "Diltiazem",
  "Dimethylformamide",
  "Diosmin",
  "Diphenhydramine",
  "Dipyridamole",
  "Disopyramide",
  "Disopyramide or Procainamide",
  "Distigmine",
  "Disulfiram",
  "Ditazole",
  "Diuretics",
  "Dobutamine",
  "Dofetilide",
  "Domperidone",
  "Doxapram",
  "Doxofylline",
  "Doxorubicin",
  "Dronedarone",
  "Drotrecogin alfa",
  "Drugs that affect calcium",
  "Drugs that affect gastric pH",
  "Drugs that affect renal clearance",
  "Drugs that alter its renal clearance",
  "Drugs that cause bone marrow suppression",
  "Drugs that cause pancreatitis",
  "Drugs that lower potassium levels",
  "Drugs that prolong the QT interval",
  "Duloxetine",
  "Dutasteride",
  "Dutasteride or Finasteride",
  "Echinocandins",
  "Ecothiopate iodide",
  "Edible fungi",
  "Edrophonium",
  "Emergency hormonal contraceptives",
  "Endothelin receptor antagonists",
  "Enfuvirtide",
  "Enoximone",
  "Entecavir",
  "Enteral feeds or Food",
  "Enzastaurin",
  "Enzyme inducers",
  "Ephedrine",
  "Eplerenone",
  "Epoetins",
  "Epoprostenol",
  "Ergot derivatives",
  "Erlotinib",
  "Erythromyci",
  "Erythromycin",
  "Eslicarbazepine",
  "Estramustine",
  "Etanercept",
  "Ethambutol",
  "Ethchlorvynol",
  "Ethionamide",
  "Ethosuximide",
  "Ethylene dibromide",
  "Etoposide",
  "Evening primrose oil",
  "Everolimus",
  "Exemestane",
  "Exenatide",
  "Ezetimibe",
  "Famciclovir",
  "Febuxostat",
  "Felbamate",
  "Felodipine",
  "Fenfluramine",
  "Fenoldopam",
  "Fibrates",
  "Fibre or Pectin",
  "Fish oils",
  "Flecainide",
  "Fluconazole",
  "Flucytosine",
  "Fludarabine",
  "Fludarabine with Cytarabine",
  "Flunarizine",
  "Fluorouracil",
  "Fluorouracil and related prodrugs",
  "Fluorouracil prodrugs",
  "Fluoxetine",
  "Fluoxetine and Droperidol",
  "Flupentixol and related drugs",
  "Flupirtine",
  "Flutamide",
  "Fluvastatin",
  "Fluvoxamine",
  "Folic acid",
  "Folinates",
  "Fondaparinux",
  "Food",
  "Food or Guar gum",
  "Foscarnet",
  "Fosfomycin",
  "Fosphenytoin",
  "Fulvestrant",
  "Furazolidone",
  "Furosemide",
  "Fusidic acid",
  "Gabapentin",
  "Ganciclovir",
  "Ganciclovir or Valganciclovir",
  "Garlic",
  "Gemcitabine",
  "Gemfibrozil",
  "Gestrinone",
  "Geum chiloense",
  "Ginger",
  "Ginseng",
  "Glucagon",
  "Glutethimide",
  "Gold",
  "Granisetron",
  "Grapefri",
  "Grapefruit",
  "Grapefruit and other fruit juices",
  "Grapefruit jui",
  "Grapefruit juice",
  "Griseofulvin",
  "Guanadrel",
  "Guanethidine",
  "Guanethidine and related drugs",
  "Guanfacine",
  "Guar gum or Glucomannan",
  "HRT",
  "Halofantrine",
  "Haloperidol",
  "Haloperidol and related drugs",
  "Heparin",
  "Heparin and LMWHs",
  "Heparinoids",
  "Heparins",
  "Herbal medicines",
  "Herbal medicines or Foods",
  "Herbicides",
  "Hormonal contraceptives",
  "Hormonal contraceptives and Progestogens",
  "Hormonal contraceptives or HRT",
  "Hormonal contraceptives or Sex hormones",
  "Hydralazine",
  "Hydrochlorothiazide",
  "Hydroxycarbamide",
  "Ibuprofen",
  "Ibutilide",
  "Idenafil",
  "Idoxuridine",
  "Idrocilamide",
  "Imatinib",
  "Imatinib and Sunitinib",
  "Imipenem",
  "Imipramine",
  "Immunoglobulins",
  "Immunosuppressants",
  "Indanediones",
  "Indinavir",
  "Indometacin",
  "Influenza vaccines",
  "Inotropes and Vasopressors",
  "Insect allergen extracts",
  "Insecticides",
  "Insulin",
  "Interferon alfa",
  "Interferons",
  "Ipriflavone",
  "Irbesartan",
  "Irinotecan",
  "Iron chelators",
  "Iron compounds",
  "Iron or Zinc compounds",
  "Isoniazid",
  "Isotretinoin",
  "Itraconazole",
  "Ivabradine",
  "Ivermectin",
  "Kaolin",
  "Kava",
  "Ketanserin",
  "Ketobemidone",
  "Ketoconazole",
  "Ketoconazole and other CYP3A4",
  "Ketoconazole and other CYP3A4 hi",
  "Ketoconazole and other CYP3A4 inhibitors",
  "Ketoconazole and other CYP3A4 jitors",
  "Ketotifen",
  "Lacosamide",
  "Lamivudine",
  "Lamotrigine",
  "Lanthanum",
  "Lapatinib",
  "Lasofoxifene",
  "Laxatives",
  "Leflunomide",
  "Lenalidomide",
  "Leukotriene antagonists",
  "Levamfetamine",
  "Levamisole",
  "Levetiracetam",
  "Levocarnitine",
  "Levodopa",
  "Levomepromazine",
  "Levosimendan",
  "Lidocaine",
  "Linezolid",
  "Liquorice",
  "Liraglutide",
  "Lithium",
  "Liv 52",
  "Local anaesthetics",
  "Loop diuretics",
  "Loperamide",
  "Loracarbef",
  "Loxapine",
  "Lumefantrine",
  "MAOIs",
  "MAOIs or RIMAs",
  "Macrolides",
  "Magnesium compounds",
  "Magnesium sulfate",
  "Mannitol",
  "Maprotiline",
  "Maraviroc",
  "Mazindol",
  "Mecamylamine",
  "Medroxyprogesterone",
  "Medroxyprogesterone or Megestrol",
  "Mefloquine",
  "Megestrol",
  "Melatonin",
  "Melperone",
  "Melphalan",
  "Memantine",
  "Menthol",
  "Meprobamate",
  "Mesuximide",
  "Metformin",
  "Methaqualone",
  "Methenamine",
  "Methotrexat",
  "Methotrexate",
  "Methoxsalen",
  "Methyldopa",
  "Methylnaltrexone",
  "Methylphenidate",
  "Metoclopramide",
  "Metoclopramide or Propantheline",
  "Metrifonate",
  "Metronidazole",
  "Metronidazole and related drugs",
  "Metyrapone",
  "Mexiletine",
  "Mexiletine or Tocainide",
  "Miconazole",
  "Mifepristone",
  "Milk",
  "Milk thistle",
  "Minocycline",
  "Minoxidil",
  "Mirtazapine",
  "Miscellanec",
  "Miscellaneous",
  "Misoprostol",
  "Mitomycin",
  "Mitotane",
  "Mizolastine",
  "Moclobemide",
  "Modafini",
  "Modafinil",
  "Molindone",
  "Monoclonal antibodies",
  "Monosodium glutamate",
  "Montelukast",
  "Moracizine",
  "Morphine",
  "Mosapride",
  "Moxisylyte",
  "Moxonidine",
  "Muscle relaxants",
  "Mycophenolate",
  "NNRTIs",
  "NRTIls",
  "NRTIs",
  "NSAIDs",
  "NSAIDs or Aspirin",
  "NSAIDs or Salicylates",
  "Naloxone",
  "Naltrexone",
  "Nasal decongestants",
  "Nasal decongestants and related drugs",
  "Nateglinide or Repaglinide",
  "Nefazodone",
  "Nefazodone or Trazodone",
  "Nefopam",
  "Neomycin",
  "Neuromuscular blockers",
  "Niclosamide",
  "Nicorandil",
  "Nicotine",
  "Nifedipine",
  "Nilotinib",
  "Nitrates",
  "Nitrofurantoin",
  "Nitrosoureas",
  "Nitrous oxide",
  "Nitroxoline",
  "Nystatin",
  "Octreotide",
  "Oestrogens",
  "Olanzapine",
  "Omeprazole",
  "Ondansetron",
  "Opioids",
  "Orange juice",
  "Organophosphorus compounds",
  "Orlistat",
  "Oseltamivir",
  "Oseltamivir and Zanamivir",
  "Other antibacterials",
  "Other antiepileptics",
  "Other antimycobacterials",
  "Other antineoplastics",
  "Other drugs that affect blood pressure",
  "Other drugs that affect coagulation",
  "Other drugs that prolong the QT interval",
  "Other drugs with hyperglycaemic",
  "Oxaceprol",
  "Oxaliplatin",
  "Oxazepam",
  "Oxcarbazepine",
  "Oxiracetam",
  "Oxolamine",
  "Oxybutyn",
  "Oxybutynin",
  "Oxygen",
  "Ozagrel",
  "PUVA",
  "Paliperidone",
  "Pancreatic enzymes",
  "Panitumumab",
  "Papaverine",
  "Paraldehyde",
  "Parathyroid hormones",
  "Paricalcitol",
  "Pemetrexed",
  "Pen",
  "Penicillamine",
  "Penicillins",
  "Pentamidine",
  "Pentazocine",
  "Pentostatin",
  "Pentoxifylline",
  "Perospirone",
  "Phenelzine",
  "Pheneturide",
  "Phenmetrazine",
  "Phenobarbital",
  "Phenobarbital or Phenytoin",
  "Phenobarbital or Pri",
  "Phenobarbital or Primidone",
  "Phenothiazines",
  "Phenoxybenzamine",
  "Phenylbutazone",
  "Phenylpropanolamine",
  "Phenytoi",
  "Phenytoin",
  "Phosphate binders",
  "Picotamide",
  "Pilocarpine",
  "Pimozide",
  "Pinaverium",
  "Pioglitazone or Rosiglitazone",
  "Piperazine",
  "Piracetam",
  "Pirenzepine",
  "Piribedil",
  "Pirmenol",
  "Pizotifen",
  "Pneumococcal vaccine",
  "Policosanol",
  "Polycarbophil calcium",
  "Polystyrene sulfonate",
  "Polyvalent cations",
  "Potassium compounds",
  "Pramipexole",
  "Pramlintide",
  "Prasugrel",
  "Praziquantel",
  "Prazosin",
  "Prednisolone",
  "Prednisone",
  "Pregabalin",
  "Pri idone",
  "Primaquine",
  "Primidone",
  "Probenecid",
  "Probucol",
  "Procainamide",
  "Procarbazine",
  "Prochlorperazine",
  "Progabide",
  "Proguanil",
  "Prolintane",
  "Propafenone",
  "Propantheline",
  "Propofol",
  "Propranolol",
  "Prostaglandins",
  "Protease",
  "Protease i",
  "Protease ii",
  "Protease inhi",
  "Protease inhibit",
  "Protease inhibitors",
  "Protease inhibits",
  "Protionamide",
  "Proton pump in",
  "Proton pump inhibi",
  "Proton pump inhibitors",
  "Proton pump inhibitors and other CYP2C19 inhibitors",
  "Pseudoephedrine",
  "Pseudoephedrine and related drugs",
  "Psoralens",
  "Pyrantel",
  "Pyrazinamide",
  "Pyridoxal",
  "Pyrimethamine",
  "Quetiapine",
  "Qui",
  "Qui ine",
  "Qui line",
  "Quilinggao",
  "Quinapril",
  "Quinidi",
  "Quinidine",
  "Quinidine or Quinine",
  "Quinine",
  "Quinine and related drugs",
  "Quinolones",
  "Quit",
  "Raloxifene",
  "Raltegravir",
  "Raltitrexed",
  "Ramelteon",
  "Rani",
  "Ranitidine",
  "Ranolazine",
  "Rasagiline",
  "Rauwolfia alkaloids",
  "Rauwolfia alkaloids or Tetrabenazine",
  "Reboxetine",
  "Remacemide",
  "Repaglinide",
  "Reserpine",
  "Reserpir",
  "Retapamulin",
  "Retigabine",
  "Retinoids",
  "Ribaviri",
  "Ribavirin",
  "Rifabutin",
  "Rifam",
  "Rifampici",
  "Rifamycins",
  "Rifaximin",
  "Rimantadine",
  "Rimonabant",
  "Risperidone",
  "Ritanserin",
  "Ritodrine",
  "Ritonavir",
  "Rivaroxaban",
  "Roflumilast",
  "Ropinirole",
  "Rotigotine",
  "Royal jelly",
  "Rufinamide",
  "SNRIs",
  "SSRIs",
  "SSRIs and related antidepressants",
  "SSRIs or SNRIs",
  "Salicylates",
  "Schisandra",
  "Selenium",
  "Semaxanib",
  "Senna",
  "Serotonergic drugs",
  "Sertindole",
  "Sertraline",
  "Sevelamer",
  "Sibutramine",
  "Sirolimus",
  "Sirolimus and related drugs",
  "Sirolimus or Tacrolimus",
  "Sodium bicarbonate",
  "Sodium compounds",
  "Sodium edetate",
  "Sodium nitroprusside",
  "Sodium oxybate",
  "Somatostatin analogue",
  "Somatostatin analogues",
  "Somatropin",
  "Sorafenib",
  "Sorbitol",
  "Sorivudine",
  "Spermicides",
  "Spiramycin",
  "Spironolactone",
  "St",
  "Statins",
  "Stiripentol",
  "Streptozocin",
  "Strontium ranelate",
  "Succimer",
  "Sucralfate",
  "Sucrose polyesters",
  "Sugammadex",
  "Sulfasalazine",
  "Sulfinpyrazone",
  "Sulfiram",
  "Sulfonamides",
  "Sulfonylureas",
  "Sulpiride",
  "Sultiame",
  "Sunitinib",
  "Sympathomimetics",
  "Tacrine",
  "Tacrolimus",
  "Tacrolimus or Pimecrolimus",
  "Tadalafil",
  "Tamarindus indica",
  "Tamoxifen",
  "Tamoxifen or Toremifene",
  "Tamsulosin",
  "Taxanes",
  "Tegafur with Uracil",
  "Tegaserod",
  "Teicoplanin",
  "Telbivudine",
  "Temozolomide",
  "Temsirolimus",
  "Tenofovir",
  "Terbinafine",
  "Terbutaline",
  "Terfenadine",
  "Testosterone",
  "Tetrabenazine",
  "Tetracyclic and related antidepressants",
  "Tetracyclic antidepressants",
  "Tetracycline",
  "Tetracyclines",
  "Thalidomide",
  "Theophylline",
  "Theophylline or Diprophylline",
  "Thiazide diuretics",
  "Thiazolidinediones",
  "Thioctic acid",
  "Thiomersal",
  "Thiopurines",
  "Thiotepa",
  "Thrombin inhibitors",
  "Thrombolytics",
  "Thyroid and Antithyroid compounds",
  "Thyroid hormones",
  "Thyroid hormones and Antithyroid drugs",
  "Tiabendazole",
  "Tiagabine",
  "Tianeptine",
  "Tibolone",
  "Ticlopi",
  "Ticlopidine",
  "Tiludronate",
  "Timolol",
  "Tioguanine",
  "Tiotixene",
  "Tirilazad",
  "Tizani",
  "Tizanidine",
  "Tobacco",
  "Tobacco or",
  "Tobacco or Cannabis",
  "Tobacco or Nicotine",
  "Tocainide",
  "Tolazoline",
  "Tolterodine",
  "Tolvaptan",
  "Topiramate",
  "Topotecan",
  "Toremifene",
  "Trabectedin",
  "Tramadol",
  "Tranylcypromine",
  "Trastuzumab",
  "Trazodone",
  "Tretinoin",
  "Trichloroethylene",
  "Tricyclic and related antidepressants",
  "Tricyclic antidepressants",
  "Trientine",
  "Trifluoperazine",
  "Trimetaphan",
  "Trimetazidine",
  "Trimethoprim",
  "Triptans",
  "Troleandomycin",
  "Trospium",
  "Tryptophan",
  "Tumour necrosis factor antagonists",
  "Tyramine",
  "Ulinastatin",
  "Urapidil",
  "Uricosuric drugs",
  "Urinary acidifiers or alkalini",
  "Urinary acidifiers or alkalinisers",
  "Urinary alkalinisers",
  "Urinary antimuscarinics",
  "Vaccines",
  "Valaciclovir",
  "Valnoctamide",
  "Valproate",
  "Valspodar",
  "Vancomycin",
  "Vardenafil",
  "Varenicline",
  "Vasodilators",
  "Vasopressin",
  "Venlafaxine",
  "Verapami",
  "Verapamil",
  "Vidarabine",
  "Vigabatrin",
  "Viloxazine",
  "Vinca alkaloids",
  "Vinpocetine",
  "Vitamin E substances",
  "Vitamin K substances",
  "Vitamins",
  "Voriconazole",
  "Vorinostat",
  "Xanthines",
  "Yohimbine",
  "Zafirlukast",
  "Ziconotide",
  "Zidovudine",
  "Zileuton",
  "Zinc compounds",
  "Zinc sulphate",
  "Ziprasidone",
  "Zonisamide",
  "Zopiclone",
  "Zotepine",
  "dine",
  "ediones",
  "euromuscular blockers",
  "hium",
  "iabetics",
  "ibutramine",
  "ice Cabergoline",
  "iclosporin",
  "id",
  "ide",
  "idine",
  "idocaine",
  "ids",
  "ie",
  "igabatrin",
  "igoxin",
  "imozide",
  "in or other Salicylates",
  "ine",
  "inezolid",
  "inine",
  "irenzepine",
  "isphosphonates",
  "itors",
  "ium",
  "izanidine",
  "jigoxin",
  "lIfosfamide",
  "limus",
  "lrinotecan",
  "lron chelators",
  "lron compounds",
  "lsoniazid",
  "mus and related drugs",
  "ombined hormonal contraceptives",
  "op diuretics",
  "ors",
  "seltamivir and Zanamivir",
  "st"
]

client = Groq(api_key="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")

class DrugListPayload(BaseModel):
    drugs: List[str]

class QueryPayload(BaseModel):
    question: str

@app.post("/query")
async def query_drug_class(payload: QueryPayload):
    if not drug_list:
        raise HTTPException(status_code=400, detail="Drug list is empty. Please set it first.")
    
    # Format the drug list into a string for prompt
    drugs_str = ", ".join(f'"{drug}"' for drug in drug_list)
    
    system_message = (
        "If the drug is in the list, respond with the drug name. "
        "Otherwise, respond only with the drug’s class. If the class is not known or the drug is not in the list, respond with ‘unknown’"
    )
    
    user_message = f"{payload.question}\n[{drugs_str}]"

    try:
        chat_completion = client.chat.completions.create(
            messages=[
                {"role": "system", "content": system_message},
                {"role": "user", "content": user_message}
            ]
        )
        # Extract response content from Groq API
        response_text = chat_completion.choices[0].message["content"]
        return {"answer": response_text}
    except Exception as e:
        raise HTTPException(status_code=500, detail=str(e))